<a href="https://colab.research.google.com/github/sd3ntato/ISPR_Project/blob/main/btc.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

This project consists in using DeepESN and (possibly)GruESN to predict bitcoin stock market price.

I use a dataset from kaggle that reports price minute by minute.

#preliminary stuff 

In [1]:
# reference to dataset:
# https://www.kaggle.com/mczielinski/bitcoin-historical-data

# mainstream libraries
import numpy as np
import pandas as pd
import math
import plotly.graph_objects as go
from IPython.display import clear_output


# i need code and data from my drive
from google.colab import drive
drive.mount('/content/drive', force_remount=True)

# import code for ESN, DeepESN, GruESN from drive
import sys
sys.path.append('/content/drive/Othercomputers/Il mio MacBook Air/SimpleESN')
sys.path.append('/content/drive/Othercomputers/Il mio MacBook Air/ISPR_Project')
from Simple_ESN import ESN, MSE
from functions import *


Mounted at /content/drive


##lettura and visualization

In [2]:
# read the dataset with data minute by minute.
data = pd.read_csv("/content/drive/MyDrive/ISPR/bitstampUSD_1-min_data_2012-01-01_to_2021-03-31.csv")
data = data.dropna(how='any') # na slots are when price does not change.
data.index = pd.RangeIndex(len(data.index))

from datetime import datetime
timestamps = data['Timestamp'].to_numpy().tolist()
dates = list([datetime.fromtimestamp( t ) for t in timestamps])
data['Dates'] = dates

print(f'total number of samples given: {len(data)}')

# we take for example the last 10 000 (approximately 10 weeks) and the same amount for testing
data = data[-13000:]
data

total number of samples given: 3613769


Timestamp      Open  ...  Weighted_Price               Dates
3600769  1616366520  57747.16  ...    57759.129449 2021-03-21 22:42:00
3600770  1616366580  57776.54  ...    57736.569842 2021-03-21 22:43:00
3600771  1616366640  57764.47  ...    57774.318362 2021-03-21 22:44:00
3600772  1616366700  57748.37  ...    57760.980994 2021-03-21 22:45:00
3600773  1616366760  57792.07  ...    57800.905108 2021-03-21 22:46:00
...             ...       ...  ...             ...                 ...
3613764  1617148560  58714.31  ...    58692.753339 2021-03-30 23:56:00
3613765  1617148620  58683.97  ...    58693.226508 2021-03-30 23:57:00
3613766  1617148680  58693.43  ...    58696.198496 2021-03-30 23:58:00
3613767  1617148740  58742.18  ...    58761.866202 2021-03-30 23:59:00
3613768  1617148800  58767.75  ...    58764.349363 2021-03-31 00:00:00

[13000 rows x 9 columns]

In [3]:
# visualize and work on some of the data:
fig = go.Figure(data=[go.Candlestick(x=data['Dates'],
                open=data['Open'],
                high=data['High'],
                low=data['Low'],
                close=data['Close'])])

fig.show()

##Preprocessing
shift the data separating input from target output, than separate training, validation and test data.

In [4]:
# temporal shift: we try and predict the price r minutes ahead.
r = 3

# put data inside a matrix, only ohlc values
dataset_x = data[['Open','High','Low','Close']].to_numpy()

# normalize data to 0 mean and 1 variance
dataset_x = normalize(dataset_x)

# separate input data from output data: output data is shifted to the left by r positions,
# so that it goes ahead by r temporal steps w.r.t. dataset_x . 
dataset_y = np.roll(dataset_x,-r,axis=0)

# discard rolled positions because they are not meaningfull anymore
dataset_x = dataset_x[r:np.size(dataset_x)-r]
dataset_y = dataset_y[r:np.size(dataset_y)-r]

# y[t] = x[t+r]  
# y[t] is r steps in the future w.r.t. x[t]
for t in range(np.size(dataset_x,axis=0)-r):
  assert np.linalg.norm(dataset_x[t+r] - dataset_y[t])==0.0

# separate training data from validation and test.
train_x = dataset_x[:4000]
train_y = dataset_y[:4000]

valid_x = dataset_x[4000:5000]
valid_y = dataset_y[4000:5000]


test_x = dataset_x[5000:]
test_y = dataset_y[5000:]

print(f'\nDATA SHAPES \ntraining data: {np.shape(train_x)},{np.shape(train_y)},\nvalid data: {np.shape(valid_x)},{np.shape(valid_y)}, \ntest data: {np.shape(test_x)}, {np.shape(test_y)}')


DATA SHAPES 
training data: (4000, 4),(4000, 4),
valid data: (1000, 4),(1000, 4), 
test data: (7997, 4), (7997, 4)


# LOCAL IMPLEMENTATIONS

In [5]:
# When working with my implementation of ESN, the convention is that every data point is a column vector
# reshape data so that each data point is a column vector, we have a tensor containing datapoints in the form of column vector
train_x = train_x.reshape(-1,4,1)
train_y = train_y.reshape(-1,4,1)
valid_x = valid_x.reshape(-1,4,1)
valid_y = valid_y.reshape(-1,4,1)
test_x = test_x.reshape(-1,4,1)
test_y = test_y.reshape(-1,4,1)

## ESN shallow

In [6]:
# now that we got the data ready, we can go ahead and train a network on it, then asses the results. 
# We start with an initial very simple trial using a shallow ESN, just to see if the framework is working.
n = ESN(Nu=4, Ny=4,rho =0.9, Nr=100, r_density =0.1, i_density =1)
n.train(train_x[501:],train_y[501:],train_x[:500])
err , out = n.score(test_x,test_y)
print(f'MSE on test dataset: {err}')

MSE on test dataset: 0.0020785984863144103


In [7]:
# we arrange the obtained data in dataframes so that we can pretty-plot them
real = ohlc_matrix_to_dataframe(test_y.reshape(-1,4)) 
predicted = ohlc_matrix_to_dataframe(out.reshape(-1,4),r=r)

# then actually plot the results:
# we plot candlestick graph with a bar indicating the predicted Low value.

fig = plot_comparison_candlesticks_with_predicted_low(real, predicted)
fig.show()

## DeepESN readout concat

In [8]:
from SimpleDeepESN import DeepESN
n = DeepESN(Nu=4, Ny=4,N=3,Nr=50,rho=0.9)
n.train_concat(train_x[501:],train_y[501:],train_x[:500])
err , out = n.score_concat(test_x,test_y)
print(f'MSE on test dataset: {err}')

MSE on test dataset: 0.0023582868067450248


In [9]:
# we arrange the obtained data in dataframes so that we can pretty-plot them
real = ohlc_matrix_to_dataframe(test_y.reshape(-1,4)) 
predicted = ohlc_matrix_to_dataframe(out.reshape(-1,4),r=r)

# then actually plot the results:
# we plot candlestick graph with a bar indicating the predicted Low value.

fig = plot_comparison_candlesticks_with_predicted_low(real, predicted)
fig.show()

##DeepESN readout ultimo layer

In [10]:
from SimpleDeepESN import DeepESN
n = DeepESN(Nu=4, Ny=4,N=5,Nr=20)
n.train(train_x[501:],train_y[501:],train_x[:500],2)
err , out = n.score(test_x,test_y,2)
print(f'MSE on test dataset: {err}')

MSE on test dataset: 0.0025786222805357943


In [11]:
# we arrange the obtained data in dataframes so that we can pretty-plot them
real = ohlc_matrix_to_dataframe(test_y.reshape(-1,4)) 
predicted = ohlc_matrix_to_dataframe(out.reshape(-1,4),r=r)

# then actually plot the results:
# we plot candlestick graph with a bar indicating the predicted Low value.

fig = plot_comparison_candlesticks_with_predicted_low(real, predicted)
fig.show()

# keras

## GruESN

In [12]:
import tensorflow as tf
import tensorflow.keras as keras

class GruESNRZCell(keras.layers.Layer):
  def __init__(self, units, **kwargs):

    self.state_size = units
    super().__init__(**kwargs)

  def build(self, input_shape):
    
    self.Wrin = self.add_weight( shape=(input_shape[-1], self.state_size), initializer="uniform", trainable =True)

    self.Wr = self.add_weight(shape=(self.state_size, self.state_size), initializer="uniform", trainable =True)

    self.Wzin = self.add_weight(shape=(input_shape[-1], self.state_size), initializer="uniform", trainable =True)

    self.Wz = self.add_weight(shape=(self.state_size, self.state_size), initializer="uniform", trainable =True)

    self.Win = self.add_weight(shape=(input_shape[-1], self.state_size), initializer="uniform", trainable =False)

    self.W = self.add_weight(shape=(self.state_size, self.state_size), initializer="uniform", trainable =False)

    self.built = True
    
  def call(self, inputs, states):

    u = inputs
    x_tm1 = states[0]

    r = tf.math.sigmoid( tf.matmul(inputs, self.Wrin ) + tf.matmul( x_tm1, self.Wr) )
    z = tf.math.sigmoid( tf.matmul(inputs, self.Wzin ) + tf.matmul( x_tm1, self.Wz) )
    h = tf.math.tanh( tf.matmul(inputs, self.Win) + tf.matmul( tf.math.multiply(r, x_tm1), self.W ) )
    x = tf.math.multiply( z, x_tm1) + tf.math.multiply( (tf.ones(self.state_size) - z), h  )

    return x, [x]


In [13]:
tx = train_x.reshape(-1,100,4)
ty = train_y.reshape(-1,100,4)
model = keras.models.Sequential([
      #keras.layers.GRU(100, stateful=True, return_sequences=True, batch_input_shape=(1, 10000, 4)), # stateful one
      keras.layers.RNN( GruESNRZCell(100),return_sequences=True, input_shape=(None, 4)),
      #keras.layers.GRU( 100,return_sequences=True, input_shape=(None, 4)),
      #keras.layers.Dense(100),  
      keras.layers.Dense(4), 
])
model.compile(optimizer="adam", loss="mse", sample_weight_mode="temporal",)
print(model.summary())
model.fit(tx,ty,epochs=30, batch_size=1, shuffle=False)
clear_output()

ttx = test_x.reshape(1,-1,4)
tty = test_y.reshape(1,-1,4)

out = model.predict(ttx)

# we arrange the obtained data in dataframes so that we can pretty-plot them
real = ohlc_matrix_to_dataframe(test_y.reshape(-1,4)) 
predicted = ohlc_matrix_to_dataframe(out.reshape(-1,4),r=r)

# then actually plot the results:
# we plot candlestick graph with a bar indicating the predicted Low value.

fig = plot_comparison_candlesticks_with_predicted_low(real, predicted)
fig.show()

err = MSE( out.reshape(-1,4), tty.reshape(-1,4), 500)
print(f'MSE on test dataset: {err}')

MSE on test dataset: 0.0033417797082887454


## FeedForward

In [ ]:
tx = train_x.reshape(-1,4)
ty = train_y.reshape(-1,4)

model = keras.models.Sequential([
      #keras.layers.RNN( GruESNRZCell(100),return_sequences=True, input_shape=(None,4)),
      #keras.layers.Dense( 400,input_shape=(4,), activation='relu'),
      keras.layers.Dense( 100, input_shape=(4,)),
      keras.layers.Dense(4) 
])
model.compile(optimizer="SGD", loss="mse", metrics=["mse"])
print(model.summary())
h = model.fit(tx,ty,epochs=10, batch_size=10)
#clear_output()

out = model.predict(test_x.reshape(-1,4)).reshape(-1,4,1)

# we arrange the obtained data in dataframes so that we can pretty-plot them
real = ohlc_matrix_to_dataframe(test_y, 9990) 
predicted = ohlc_matrix_to_dataframe(out,9990,r)

# then actually plot the results:
# we plot candlestick graph with a bar indicating the predicted Low value.

fig = plot_comparison_candlesticks_with_predicted_low(real, predicted)
fig.show()

In [ ]:
h.history
